<a href="https://colab.research.google.com/github/datakind/hxl-metadata-prediction/blob/main/generate-test-train-data.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Introduction

This notebook downloads data provided by the HDX team from a google drive folder. The data was captured using an [HXL crawl process](https://github.com/HXLStandard/hdx-hashtag-crawler)

# Setup

In [1]:
!pip install gdown==5.2.0
!pip install pandas==2.2.2
!pip install hdx-python-api==6.3.1

  Attempting uninstall: gdown
    Found existing installation: gdown 5.1.0
    Uninstalling gdown-5.1.0:
      Successfully uninstalled gdown-5.1.0
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 67.3 MB/s eta 0:00:00
  Attempting uninstall: pandas
    Found existing installation: pandas 2.0.3
    Uninstalling pandas-2.0.3:
      Successfully uninstalled pandas-2.0.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pandas<2.2.2dev0,>=2.0, but you have pandas 2.2.2 which is incompatible.
google-colab 1.0.0 requires pandas==2.0.3, but you have pandas 2.2.2 which is incompatible.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.9/69.9 kB 2.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.3/46.3 kB 4.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.3/42.3 kB 4.9 MB/s eta 0:00:00
  Preparing m

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [39]:
import sys
import os
import requests
import gdown
import tarfile
import pandas as pd
import re
from sklearn.model_selection import train_test_split

from hdx.utilities.easy_logging import setup_logging
from hdx.api.configuration import Configuration
from hdx.data.dataset import Dataset
import hxl
import json
import time

import numpy as np


input_options = hxl.input.InputOptions(http_headers={'User-Agent': "DK HXL Analaysis"})

# Google drive location of HDXHashtag crawler data. Shared with HDX team
DATA_GDRIVE="https://drive.google.com/file/d/1BDCuh0WVJWK1-1RMC-77cvh4H2Hep_ry/export?format=xlsx"
DATA_FILE="hdx-hxl-output.tgz"

GOOGLE_BASE_DIR = "/content/drive/MyDrive/Colab"

# This is the HXL schema sheet, search HDX to get this link
HXL_SCHEMA_RESOURCE_URL = "https://docs.google.com/spreadsheets/d/1En9FlmM8PrbTWgl3UHPF_MXnJ6ziVZFhBbojSJzBdLI/export?format=xlsx"

# Where to save local data files
LOCAL_DATA_DIR = f"{GOOGLE_BASE_DIR}/hxl-metadata-prediction/data/"

# Number of records in data excerpts
DATA_EXCERPT_SIZE = 10

local_data_file = LOCAL_DATA_DIR + "/" + DATA_FILE

pd.set_option('display.max_colwidth', 200)
pd.set_option('display.max_rows', 200)

## Get HDX connection

In [6]:
agent_count = 0

def setup_hdx_connection(agent_name):
    try:
        Configuration.create(hdx_site="prod", user_agent=agent_name, hdx_read_only=True)
    except:
        print("Configuration already created, continuing ...")

# Note, if you run this twice you will get a 'Configuration already exists!' error, but it can be ignored
setup_hdx_connection(f"DK_UserAgent{agent_count}")

## Download HXL Core schema

In [38]:
local_data_file = LOCAL_DATA_DIR + "/hxl-core-schema.xlsx"

response = requests.get(HXL_SCHEMA_RESOURCE_URL)
with open(local_data_file, 'wb') as f:
    f.write(response.content)

df= pd.read_excel(local_data_file, sheet_name='Core hashtags')
hashtags_list = df['Hashtag'][1:].tolist()

df= pd.read_excel(local_data_file, sheet_name='Core attributes')
attributes_list = df['Attribute'][1:].tolist()

# Remove rows with disallowed tags or attributes
APPROVED_HXL_SCHEMA = hashtags_list + attributes_list

print("Approved HXL schema ...")
print(APPROVED_HXL_SCHEMA)

Approved HXL schema ...
['#access', '#activity', '#adm1', '#adm2', '#adm3', '#adm4', '#adm5', '#affected', '#beneficiary', '#capacity', '#cause', '#channel', '#contact', '#country', '#crisis', '#currency', '#date', '#delivery', '#description', '#event', '#frequency', '#geo', '#group', '#impact', '#indicator', '#inneed', '#item', '#loc', '#meta', '#modality', '#need', '#operations', '#org', '#output', '#population', '#reached', '#region', '#respondee', '#sector', '#service', '#severity', '#status', '#subsector', '#targeted', '#value', '+abducted', '+acronym', '+activity', '+adolescents', '+adults', '+approved', '+ar', '+bounds', '+budget', '+canceled', '+children', '+cluster', '+code', '+converted', '+coord', '+dest', '+displaced', '+elderly', '+elevation', '+email', '+en', '+end', '+es', '+f', '+fa', '+fr', '+funder', '+hh', '+i', '+id', '+idps', '+impl', '+incamp', '+ind', '+infants', '+infected', '+injured', '+killed', '+label', '+lat', '+lon', '+m', '+ms', '+name', '+noncamp', '+num

# Analysis

## Download HXL crawler data

This data was generated using the [HDX Hashtag Crawler](https://github.com/dividor/hdx-hashtag-crawler) over several days and saved to Google drive.

In [13]:
# Use gdown to download the file
gdown.download(DATA_GDRIVE, local_data_file, quiet=False, fuzzy=True)

tar = tarfile.open(local_data_file)
tar.extractall(LOCAL_DATA_DIR)
tar.close()

Downloading...
From: https://drive.google.com/uc?id=1BDCuh0WVJWK1-1RMC-77cvh4H2Hep_ry
To: /content/drive/MyDrive/Colab/hxl-metadata-prediction/data/hdx-hxl-output.tgz
100%|██████████| 19.3M/19.3M [00:00<00:00, 201MB/s]


## Identify Unique combinations of HXL tags we want for training data

In [14]:
# Open hdx-expanded-hashed-stats.csv in data/hdx-hxl

df = pd.read_csv(LOCAL_DATA_DIR + "/output/hdx-expanded-hashed-stats.csv")

# We'll keep one row per column, Hashtag with Attributes has what we require
df.drop(columns=['Attribute', 'Hashtag'], inplace=True)
df.drop_duplicates(inplace=True)

# Remove HXL tags row in the metadata (we keep them for actual data)
df = df[1:]

display(df.head())
print(df.shape)

print("Unique data providers ...")
print(len(df["Data provider"].unique()))

print("Unique HDX resource ids ...")
print(len(df["HDX resource id"].unique()))

<ipython-input-14-fa85fc3d2575>:3: DtypeWarning: Columns (9) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(LOCAL_DATA_DIR + "/output/hdx-expanded-hashed-stats.csv")


Hashtag with Attributes           Text header Locations  \
1             #affected+hh          Total IDP HH       COD   
2        #affected+idp+ind         Total IDP IND       COD   
4       #affected+idp+male    Total IDP Male Ind       COD   
6     #affected+female+idp  Total IDP Female Ind       COD   
8  #affected+ind+returnees       Total Returnees       COD   

                              Data provider  \
1  international-organization-for-migration   
2  international-organization-for-migration   
4  international-organization-for-migration   
6  international-organization-for-migration   
8  international-organization-for-migration   

                                                                               HDX dataset id  \
1  drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
2  drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
4  drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
6  drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
8  drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   

                        HDX resource id Date created Unnamed: 9  \
1  26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
2  26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
4  26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
6  26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
8  26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   

                 Hash  
1  0x2cc7fd3129c0d18c  
2  0x2cc7fd3129c0d18c  
4  0x2cc7fd3129c0d18c  
6  0x2cc7fd3129c0d18c  
8  0x2cc7fd3129c0d18c

(487297, 9)
Unique data providers ...
120
Unique HDX resource ids ...
43074


Let's use the column hash created by the crawler to find unique combinations of tags

In [15]:
hash_count = df.groupby('Hash').size()
display(hash_count)


Hash
0x100556db35012c6b       101
0x102125f4dd16c64     190286
0x10309a2e5e2722ba       509
0x105b36aac3c9192f       693
0x105c6ee3379af31c       595
                       ...  
0xf0a7e4d9104f069         12
0xf93f0051e52a4d          28
0xfa11ad9f842a37d         17
0xfe0e278de9d0a33          1
0xfe8777dcd878424         20
Length: 644, dtype: int64

In [18]:
hash_resources = df.groupby('Hash')['HDX resource id'].nunique().sort_values(ascending=False)

for col in ['HDX resource id', 'HDX dataset id', 'Data provider']:
    hash_resources  = hash_resources .reset_index()
    hash_resources [f"Unique {col}"] = hash_resources ['Hash'].map(df.groupby('Hash')[col].unique())

display(hash_resources )

hash_resources.to_excel(f"{LOCAL_DATA_DIR}/hxl_hash_resources.xlsx", index=False)

level_0  index                Hash  HDX resource id  \
0          0      0   0x102125f4dd16c64            13858   
1          1      1  0x428a8e37940223d8             9328   
2          2      2  0x31fda1ef985b4a59             3425   
3          3      3  0x19598575d3397e19             3232   
4          4      4  0x16d2b679132fea10             2147   
..       ...    ...                 ...              ...   
639      639    639  0x22def8e1b7b0c742                1   
640      640    640  0x4b7012601f2de402                1   
641      641    641  0x4aefd35864aaa20a                1   
642      642    642   0x4acf4e36d67d877                1   
643      643    643  0x57297f722f5115a5                1   

                                                                                                                                                                                      Unique HDX resource id  \
0    [51b2e4ec-aca5-4b97-bbb7-c005175b682e, a6ef8040-3b15-47ae-9973-1dbc113673cf, f579cf0e-5535-4414-897f-2f8c05105180, 66c62464-017b-4aa6-845f-9ec2487acb82, 91e1cb98-353b-487e-a14d-b0eea783da6f, 65f38...   
1    [2e130cdf-c850-4533-b2f3-e961adbec48a, 9e160d82-691d-49a6-979b-0ff0dbb6b7a8, 002501bc-7efb-4335-b672-d045cd76bc5b, 0d0e0fc4-e4f1-49cd-ad30-42cc8dc08b74, f2c1ea93-d241-413b-8140-c009da88d912, 23e36...   
2    [9c751883-698a-4a2c-9475-ff828e9c11db, 791b69af-df57-4157-96c0-c0d8d308315e, b055f1f7-8cdc-4ff8-a412-9f54d6e56c41, 6ae8568f-449b-4b59-9ad2-79d7df94cd9c, 4f4c7462-6b13-4125-a88a-f8e9ac0c837b, abb79...   
3    [ed7b5bd2-7818-4d7a-9ff0-8ba0d97bf7d5, 8f239e93-76c0-4287-a414-3d17a5e55344, 040efd19-3d71-4e0b-8939-f6b46c465868, 8db41d1c-af8f-4f26-9d40-5b80b1bf72e8, 6482dc75-0e79-40d9-aacf-cdcde3c368a6, c9981...   
4    [295cd9e4-8464-43ee-ad17-47196991a1f7, 34337d16-017d-4d69-834c-a5e0fc21a549, b51b8c0e-494d-488b-98d5-a70fd9451b90, 75076d6a-8d3f-49e3-b4f4-7c889bc82806, 7e0b2b37-73b8-4c69-bb11-6ba954fa0cd9, 08ea0...   
..                                                                                                                                                                                                       ...   
639                                                                                                                                                                   [68328f42-9276-423e-80d0-fe89630804ff]   
640                                                                                                                                                                   [63143067-46e0-4fb5-b131-d83ee45122ab]   
641                                                                                                                                                                   [6ddcfbc9-fa06-4b14-b9a4-ce96d3fae65e]   
642                                                                                                                                                                   [903326f2-b372-4786-9973-87226cb15e41]   
643                                                                                                                                                                   [8b0feea6-20e4-45dc-aaae-c8b6fbd5a9f4]   

                                                                                                                                                                                       Unique HDX dataset id  \
0    [who-data-for-south-sudan, who-data-for-montenegro, who-data-for-zimbabwe, who-data-for-zambia, who-data-for-yemen, who-data-for-viet-nam, who-data-for-venezuela-bolivarian-republic-of, who-data-f...   
1    [world-bank-combined-indicators-for-zimbabwe, world-bank-trade-indicators-for-zimbabwe, world-bank-external-debt-indicators-for-zimbabwe, world-bank-climate-change-indicators-for-zimbabwe, world-b...   
2    [dhs-data-for-sao-tome-and-principe, dhs-data-for-rwanda, dhs-data-for-philippines, dhs-data-for-peru, dhs-data-for-paraguay, dhs-data-for-papua-new-guinea, d

In [19]:
# Extract a single resource_id for each hash
resource_ids = hash_resources['Unique HDX resource id'].apply(lambda x: x[0])
print(resource_ids)

0      51b2e4ec-aca5-4b97-bbb7-c005175b682e
1      2e130cdf-c850-4533-b2f3-e961adbec48a
2      9c751883-698a-4a2c-9475-ff828e9c11db
3      ed7b5bd2-7818-4d7a-9ff0-8ba0d97bf7d5
4      295cd9e4-8464-43ee-ad17-47196991a1f7
                       ...                 
639    68328f42-9276-423e-80d0-fe89630804ff
640    63143067-46e0-4fb5-b131-d83ee45122ab
641    6ddcfbc9-fa06-4b14-b9a4-ce96d3fae65e
642    903326f2-b372-4786-9973-87226cb15e41
643    8b0feea6-20e4-45dc-aaae-c8b6fbd5a9f4
Name: Unique HDX resource id, Length: 644, dtype: object


In [20]:
df_subset = df[df['HDX resource id'].isin(resource_ids)]

print("Column data subset to one resource ID per hash ...")
print(df_subset.shape)

print("Unique data providers ...")
print(len(df_subset["Data provider"].unique()))

print("Unique HDX resource ids ...")
print(len(df_subset["HDX resource id"].unique()))

Column data subset to one resource ID per hash ...
(7834, 9)
Unique data providers ...
119
Unique HDX resource ids ...
644


### Download data excerpts

Using our subset of resource_ids for each hash, extract column data excerpts.

In [21]:
df2 = df_subset.copy()

df2['Data excerpt'] = ''

datasets_resources = df2[['HDX dataset id', 'HDX resource id']].drop_duplicates()
datasets_resources.reset_index(drop=True, inplace=True)

print("For each resource, extract a data excerpt for each column ...")

num_rows = datasets_resources.shape[0]
for index, row in datasets_resources.iterrows():

    if index % 10 == 0:
        print(f"Processing {index} of {num_rows} ({(index/num_rows)*100:.2f}%)")

    dataset_id = row['HDX dataset id']
    resource_id = row['HDX resource id']
    dataset = Dataset.read_from_hdx(dataset_id)
    if dataset is None:
        print(f"Dataset {dataset_id} not found!")
        continue
    resources = dataset.get_resources()
    for resource in resources:
        if resource['id'] == resource_id:
            print(f"    Accessing data for resource {resource_id}, {resource['name']}")
            try:
                url, path = resource.download(LOCAL_DATA_DIR)
                df2.loc[df2['HDX resource id'] == resource_id, 'File'] = path
                df2.loc[df2['HDX resource id'] == resource_id, 'URL'] = url

                with hxl.data(resource['url'], input_options) as source:
                    columns = [column.header for column in source.columns]
                    tags = [column.get_display_tag(sort_attributes=True) for column in source.columns]
                    data = {}
                    rowcount = 0
                    for row in source:
                        if rowcount > DATA_EXCERPT_SIZE:
                            break
                        i = 0
                        for colvalue in row:
                            colname = columns[i]
                            if colname not in data:
                                data[colname] = [colvalue]
                            else:
                                data[colname].append(colvalue)
                            i += 1
                        rowcount += 1

                    for col in columns:
                        if col in data:
                            print(f"       Setting data excerpt for column {col} >> {data[col]} ...")
                            df2.loc[(df2['HDX resource id'] == resource_id) & (df2['Text header'] == col), 'Data excerpt'] = str(data[col])

            except Exception as e:
                print(f"Error accessing data for resource {resource_id}, {resource['name']} ... {e}")

display(df2)
print(df2.shape)
df2.to_csv(f"{LOCAL_DATA_DIR}/hxl_hash_resources_data.csv", index=False)



For each resource, extract a data excerpt for each column ...
Processing 0 of 644 (0.00%)
    Accessing data for resource 26ecc26f-74e7-46af-b450-8872dca0b63b, DRC - Baseline Assessment - M23 Crisis 13 - February 2024
       Setting data excerpt for column Total IDP HH >> [319283] ...
       Setting data excerpt for column Total IDP IND >> [1548732] ...
       Setting data excerpt for column Total IDP Male Ind >> [646805] ...
       Setting data excerpt for column Total IDP Female Ind >> [901927] ...
       Setting data excerpt for column Total Returnees >> [587705] ...
    Accessing data for resource dbf9b4bd-1321-4846-b6f0-4654509d3626, admin1-summaries-earthquake.csv
       Setting data excerpt for column country_name >> ['Afghanistan', 'Afghanistan', 'Afghanistan', 'Afghanistan', 'Afghanistan', 'Afghanistan', 'Afghanistan', 'Afghanistan', 'Afghanistan', 'Afghanistan', 'Afghanistan'] ...
       Setting data excerpt for column admin1_name >> ['Kabul', 'Kapisa', 'Parwan', 'Maidan Ward

ERROR:hxl.REMOTE_ACCESS:2024-07-23 19:56:02 [error    ] Skipping column(s) with malformed hashtag specs function=parse_list hastags=name, #reporting+or+implementing+org?
ERROR:hxl.model:Skipping column(s) with malformed hashtag specs: name, #reporting+or+implementing+org?
ERROR:hxl.REMOTE_ACCESS:2024-07-23 19:56:02 [error    ] Skipping column(s) with malformed hashtag specs function=parse_list hastags=name, #reporting+or+implementing+org?
ERROR:hxl.model:Skipping column(s) with malformed hashtag specs: name, #reporting+or+implementing+org?


       Setting data excerpt for column None >> ['ACTED', 'Agency for Technical Cooperation and Development', 'INGO', 'CCCM', 'Central Equatoria', 'SS01', 'Juba', 'SS0101', 'January', 'Reporting Organization', 'ACTED', 'Agency for Technical Cooperation and Development', 'INGO', 'CCCM', 'Eastern Equatoria', 'SS02', 'Magwi', 'SS0207', 'January', 'Reporting Organization', 'ACTED', 'Agency for Technical Cooperation and Development', 'INGO', 'CCCM', 'Jonglei', 'SS03', 'Akobo', 'SS0301', 'January', 'Reporting Organization', 'ACTED', 'Agency for Technical Cooperation and Development', 'INGO', 'CCCM', 'Jonglei', 'SS03', 'Ayod', 'SS0302', 'January', 'Reporting Organization', 'HRSS', 'Hope Restoration South Sudan', 'NNGO', 'CCCM', 'Jonglei', 'SS03', 'Ayod', 'SS0302', 'January', 'Reporting Organization', 'ACTED', 'Agency for Technical Cooperation and Development', 'INGO', 'CCCM', 'Jonglei', 'SS03', 'Bor South', 'SS0303', 'January', 'Reporting Organization', 'DRC', 'Danish Refugee Council', 'INGO',

ERROR:hxl.REMOTE_ACCESS:2024-07-23 19:56:07 [error    ] Skipping column(s) with malformed hashtag specs function=parse_list hastags='activtiy+working_group
ERROR:hxl.model:Skipping column(s) with malformed hashtag specs: 'activtiy+working_group
ERROR:hxl.REMOTE_ACCESS:2024-07-23 19:56:07 [error    ] Skipping column(s) with malformed hashtag specs function=parse_list hastags='activtiy+working_group
ERROR:hxl.model:Skipping column(s) with malformed hashtag specs: 'activtiy+working_group


       Setting data excerpt for column Title >> ['Using technology to tackle child malnutrition in Zimbabwe', 'How to save mothers and newborns from preventable deaths'] ...
       Setting data excerpt for column Member Organization >> ['GOAL Global', 'FHI 360'] ...
       Setting data excerpt for column Date >> ['2021-09-03', '2023-05-09'] ...
       Setting data excerpt for column Countries >> ['', ''] ...
       Setting data excerpt for column Summary >> ["In Zimbabwe's Harare region, Covid-19's impacts on food security and limited\naccess to healthcare and nutrition education has had devastating consequences\nfor community health, particularly for children. To complement its Emergency\nSocial Cash Transfer program targeting food insecure and vulnerable\nhouseholds, GOAL partnered with UNICEF and Promobile, a private sector\npartner, to provide downloadable lifesaving nutritional videos, photos and\nrecipes through WIFI-routers mounted on trucks to help ensure that infants and\nchil

...

       Setting data excerpt for column Country >> ['Burkina Faso', 'Cameroon', 'Chad', 'Gambia', 'Mali', 'Mauritania', 'Niger', 'Nigeria', 'Senegal', 'Burkina Faso', 'Cameroon'] ...
       Setting data excerpt for column nutrition >> ['MAM', 'MAM', 'MAM', 'MAM', 'MAM', 'MAM', 'MAM', 'MAM', 'MAM', 'GAM', 'GAM'] ...
       Setting data excerpt for column Affected 2017 >> ['433,412', '209,647', '330,211', '-', '479,841', '97,632', '888,499', '506,858', '352,068', '621,582', '272,565'] ...
       Setting data excerpt for column In Need 2017 >> ['433,412', '209,647', '330,211', '-', '478,000', '73,175', '888,499', '506,858', '145,985', '621,582', '272,565'] ...
       Setting data excerpt for column Targeted 2017 >> ['             _', '98,045', '330,211', '-', '335,000', '62,199', '636,210', '253,429', '116,788', '358,073', '154,671'] ...
       Setting data excerpt for column % targeted >> ['0', '47', '100', '', '70', '85', '72', '50', '80', '58', '57'] ...
    Accessing data for resource 

ERROR:hxl.REMOTE_ACCESS:2024-07-23 21:20:43 [error    ] Skipping column(s) with malformed hashtag specs function=parse_list hastags=#sector#subsector
ERROR:hxl.model:Skipping column(s) with malformed hashtag specs: #sector#subsector
ERROR:hxl.REMOTE_ACCESS:2024-07-23 21:20:43 [error    ] Skipping column(s) with malformed hashtag specs function=parse_list hastags=#sector#subsector
ERROR:hxl.model:Skipping column(s) with malformed hashtag specs: #sector#subsector


       Setting data excerpt for column Organisación >> ['Acción Contra el Hambre', 'Adventist Development and Relief Agency', 'Arche noVa', 'Arche noVa', 'Arche noVa', 'Arche noVa', 'Arche noVa', 'International Medical Corps', 'International Medical Corps', 'International Medical Corps', 'Cooperación Técnica Belga'] ...
       Setting data excerpt for column Sector >> ['AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene', 'AguaSaneamientoHigiene'] ...
       Setting data excerpt for column Tipo de Actividad >> ['Agua', 'Higiene', 'Agua', 'Higiene', 'Saneamiento', 'Saneamiento', 'Agua', 'Saneamiento', 'Agua', 'Saneamiento', 'Agua'] ...
       Setting data excerpt for column Tcode >> ['AguaSaneamientoHigieneAgua', 'AguaSaneamientoHigieneHigiene', 'AguaSaneamientoHigieneAgua', 'AguaSane

Hashtag with Attributes           Text header Locations  \
1                  #affected+hh          Total IDP HH       COD   
2             #affected+idp+ind         Total IDP IND       COD   
4            #affected+idp+male    Total IDP Male Ind       COD   
6          #affected+female+idp  Total IDP Female Ind       COD   
8       #affected+ind+returnees       Total Returnees       COD   
...                         ...                   ...       ...   
689570                 #lat_deg               prevlat       VUT   
689571                 #lon_deg               prevlon       VUT   
689572             #period_date             datelabel       VUT   
689573                  #x_time                 hours       VUT   
689574                  #x_note                  text       VUT   

                                   Data provider  \
1       international-organization-for-migration   
2       international-organization-for-migration   
4       international-organization-for-migration   
6       international-organization-for-migration   
8       international-organization-for-migration   
...                                          ...   
689570                               brcmapsteam   
689571                               brcmapsteam   
689572                               brcmapsteam   
689573                               brcmapsteam   
689574                               brcmapsteam   

                                                                                    HDX dataset id  \
1       drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
2       drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
4       drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
6       drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
8       drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
...                                                                                            ...   
689570                                                                            cyclone-pam-path   
689571                                                                            cyclone-pam-path   
689572                                                                            cyclone-pam-path   
689573                                                                            cyclone-pam-path   
689574                                                                            cyclone-pam-path   

                             HDX resource id Date created Unnamed: 9  \
1       26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
2       26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
4       26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
6       26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
8       26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       true   
...                                      ...          ...        ...   
689570  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
689571  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
689572  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
689573  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
689574  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   

                      Hash  \
1       0x2cc7fd3129c0d18c   
2       0x2cc7fd3129c0d18c   
4       0x2cc7fd3129c0d18c   
6       0x2cc7fd3129c0d18c   
8       0x2cc7fd3129c0d18c   
...                    ...   
689570  0x1d4a8deeb40f76ce   
689571  0x1d4a8deeb40f76ce   
689572  0x1d4a8deeb40f76ce   
689573  0x1d4a8deeb40f76ce   
689574  0x1d4a8deeb40f76ce   

                                                                                                          Data excerpt  \
1    

(7834, 12)


### Train and test data

In this section we will create train and test datasets for fine tuning.

In [40]:
data = pd.read_csv(f"{LOCAL_DATA_DIR}/hxl_hash_resources_data.csv")
print(data.shape)
display(data)

(7834, 12)


Hashtag with Attributes           Text header Locations  \
0                #affected+hh          Total IDP HH       COD   
1           #affected+idp+ind         Total IDP IND       COD   
2          #affected+idp+male    Total IDP Male Ind       COD   
3        #affected+female+idp  Total IDP Female Ind       COD   
4     #affected+ind+returnees       Total Returnees       COD   
...                       ...                   ...       ...   
7829                 #lat_deg               prevlat       VUT   
7830                 #lon_deg               prevlon       VUT   
7831             #period_date             datelabel       VUT   
7832                  #x_time                 hours       VUT   
7833                  #x_note                  text       VUT   

                                 Data provider  \
0     international-organization-for-migration   
1     international-organization-for-migration   
2     international-organization-for-migration   
3     international-organization-for-migration   
4     international-organization-for-migration   
...                                        ...   
7829                               brcmapsteam   
7830                               brcmapsteam   
7831                               brcmapsteam   
7832                               brcmapsteam   
7833                               brcmapsteam   

                                                                                  HDX dataset id  \
0     drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
1     drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
2     drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
3     drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
4     drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
...                                                                                          ...   
7829                                                                            cyclone-pam-path   
7830                                                                            cyclone-pam-path   
7831                                                                            cyclone-pam-path   
7832                                                                            cyclone-pam-path   
7833                                                                            cyclone-pam-path   

                           HDX resource id Date created Unnamed: 9  \
0     26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       True   
1     26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       True   
2     26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       True   
3     26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       True   
4     26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       True   
...                                    ...          ...        ...   
7829  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
7830  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
7831  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
7832  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
7833  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   

                    Hash  \
0     0x2cc7fd3129c0d18c   
1     0x2cc7fd3129c0d18c   
2     0x2cc7fd3129c0d18c   
3     0x2cc7fd3129c0d18c   
4     0x2cc7fd3129c0d18c   
...                  ...   
7829  0x1d4a8deeb40f76ce   
7830  0x1d4a8deeb40f76ce   
7831  0x1d4a8deeb40f76ce   
7832  0x1d4a8deeb40f76ce   
7833  0x1d4a8deeb40f76ce   

                                                                                                        Data excerpt  \
0                                                                                                           [319283]   
1    

#### Data Cleaning

In [41]:
data = data[data['Data excerpt'].notnull()]
data = data[data['Data excerpt'].str.contains(r'[A-Za-z0-9]')]

print(data.shape)

(6725, 12)


#### Remove disallowed HXL

In [42]:
def filter_for_schema(text):
    #print(f"Tokens before: {text}")
    if " " in text:
        text = text.replace(" ","")

    tokens_raw = text.split("+")
    tokens = [tokens_raw[0]]
    for t in tokens_raw[1:]:
        tokens.append(f"+{t}")

    filtered = []
    for t in tokens:
        if t in APPROVED_HXL_SCHEMA:
            if t not in filtered:
                filtered.append(t)
    filtered = "".join(filtered)

    if len(filtered) > 0 and filtered[0] != '#':
        filtered = ""

    # Add spaces back in
    # filtered = filtered.replace("+", " +")

    #print(f"        After: {filtered}")
    return filtered

def filter_disallowed_hxl(column_data, hxl_col = 'Hashtag with Attributes'):
    print("Before",column_data.shape)
    allowed = []
    disallowed = []
    for index, row in column_data.iterrows():
        if row[hxl_col] == filter_for_schema(row[hxl_col]):
            allowed.append(row)
        else:
            disallowed.append(row)
    allowed = pd.DataFrame(allowed)
    disallowed = pd.DataFrame(disallowed)
    print("After", allowed.shape)
    return allowed, disallowed

data, disallowed = filter_disallowed_hxl(data)
print(data.shape)

display(disallowed)

Before (6725, 12)
After (3356, 12)
(3356, 12)


Hashtag with Attributes           Text header Locations  \
1          #affected+idp+ind         Total IDP IND       COD   
2         #affected+idp+male    Total IDP Male Ind       COD   
3       #affected+female+idp  Total IDP Female Ind       COD   
15         #meta+appeal+type                 atype       SSD   
18           #meta+appeal+id                  code       SSD   
...                      ...                   ...       ...   
7829                #lat_deg               prevlat       VUT   
7830                #lon_deg               prevlon       VUT   
7831            #period_date             datelabel       VUT   
7832                 #x_time                 hours       VUT   
7833                 #x_note                  text       VUT   

                                 Data provider  \
1     international-organization-for-migration   
2     international-organization-for-migration   
3     international-organization-for-migration   
15                                        ifrc   
18                                        ifrc   
...                                        ...   
7829                               brcmapsteam   
7830                               brcmapsteam   
7831                               brcmapsteam   
7832                               brcmapsteam   
7833                               brcmapsteam   

                                                                                  HDX dataset id  \
1     drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
2     drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
3     drc-displacement-idps-returnees-m23-crisis-north-kivu-province-baseline-assessment-iom-dtm   
15                                                             ifrc-appeals-data-for-south-sudan   
18                                                             ifrc-appeals-data-for-south-sudan   
...                                                                                          ...   
7829                                                                            cyclone-pam-path   
7830                                                                            cyclone-pam-path   
7831                                                                            cyclone-pam-path   
7832                                                                            cyclone-pam-path   
7833                                                                            cyclone-pam-path   

                           HDX resource id Date created Unnamed: 9  \
1     26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       True   
2     26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       True   
3     26ecc26f-74e7-46af-b450-8872dca0b63b   2023-10-16       True   
15    4110b824-3338-453f-ae5d-89ca80f5b147   2023-03-13       True   
18    4110b824-3338-453f-ae5d-89ca80f5b147   2023-03-13       True   
...                                    ...          ...        ...   
7829  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
7830  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
7831  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
7832  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   
7833  a8ccd9d2-8328-487a-b04b-ca3f3f2e0ea3   2015-03-16       True   

                    Hash  \
1     0x2cc7fd3129c0d18c   
2     0x2cc7fd3129c0d18c   
3     0x2cc7fd3129c0d18c   
15     0x1d1434ee319a1be   
18     0x1d1434ee319a1be   
...                  ...   
7829  0x1d4a8deeb40f76ce   
7830  0x1d4a8deeb40f76ce   
7831  0x1d4a8deeb40f76ce   
7832  0x1d4a8deeb40f76ce   
7833  0x1d4a8deeb40f76ce   

                                                                                                                              Data excerpt  \
1                                                                                                                 

#### Plot tags

In [43]:
data['tag'] = data['Hashtag with Attributes'].apply(lambda x: x.split('+')[0])
tag_counts_train = data['tag'].value_counts()

print(tag_counts_train)

tag
#adm1           527
#adm2           477
#affected       380
#country        285
#date           242
#org            231
#adm3           188
#inneed         141
#sector         110
#geo            106
#targeted        77
#loc             67
#activity        65
#status          60
#population      57
#indicator       55
#region          49
#meta            42
#reached         36
#adm4            32
#event           14
#subsector       12
#beneficiary     12
#cause           11
#item            10
#value           10
#severity         9
#output           8
#crisis           6
#service          4
#currency         4
#adm5             4
#contact          4
#access           4
#description      3
#capacity         3
#impact           3
#frequency        2
#group            2
#modality         2
#delivery         1
#operations       1
Name: count, dtype: int64


#### Generate training prompts

####  Split by data provider organization

On HDX, the hierarchy is ...

Organization > datasets > resources > tables

A random train/test split will result in data from files in a dataset being in both train and test, which would pollute the test set with very similar data to training. So we will split by organization

In [44]:
def split_data(column_data, provider_col, test_size=0.2, random_state=42):
    """
    Perform train-test split on datasets, print information, and return X_train and X_test.

    The split is done by organizations, to try and avoid the situation where an org provides
    similar data files. Also, we exclude orgs which are subsidiaries from the test set, eg ocha-*
    as presumably each subsid will provide similar data. The aim is that the test set is new.

    Parameters:
    - column_data (pd.DataFrame): DataFrame containing column data.
    - provider_col (string): Name of column holding data providers.
    - test_size (float): The proportion of the dataset to include in the test split.
    - random_state (int): Seed for random number generation.

    Returns:
    - pd.DataFrame, pd.DataFrame: X_train, X_test
    """

    orgs_df = column_data.groupby(provider_col)[provider_col].count().sort_values(ascending=False)
    orgs_df = column_data.groupby(provider_col)[provider_col].count().sort_values(ascending=False).reset_index(name='count')
    all_orgs = orgs_df[provider_col].unique()

    # Split orgs to get 'Parent', eg 'ocha-*' -> 'ocha'
    orgs_df['org_parent'] = orgs_df[provider_col].str.split('-').str[0]

    # Count occurrences of each 'org_parent'
    org_parent_counts = orgs_df['org_parent'].value_counts().reset_index(name='count')

    # Filter to keep only those occurring once
    org_parents_single_occurrence = org_parent_counts[org_parent_counts['count'] == 1]

    # Get the 'org_parent' values that occur only once
    single_occurrence_org_parents = org_parents_single_occurrence['org_parent'].tolist()

    # Filter the original DataFrame to keep rows where 'org_parent' occurs only once
    org_parents_unique = orgs_df[orgs_df['org_parent'].isin(single_occurrence_org_parents)]

    print("\nOrgs which don't seem to be subsidiaries ...\n")
    display(org_parents_unique)

    single_entities = list(org_parents_unique[provider_col].unique())

    # Remove 'hdx' from single_entities, not good for testing as it's the folks that made HXL! Also some monolithic orgs with very similar data
    single_entities = [x for x in single_entities if not x in ['hdx','ourairports']]

    single_entities.sort()

    # Sample single-subsid orgs
    sample_size = int(len(single_entities)*test_size) - 1
    np.random.seed(42)
    X_test_orgs = np.random.choice(single_entities, sample_size)
    X_train_orgs = list(set(all_orgs)-set(X_test_orgs))

    print(f"Train orgs: {X_train_orgs}")
    print(f"Test orgs: {X_test_orgs}")

    # Extract column rows for datasets in X_train_datasets
    X_train = column_data[column_data[provider_col].isin(X_train_orgs)]

    # Extract column rows for datasets in X_test_datasets
    X_test = column_data[~column_data[provider_col].isin(X_train_orgs)]

    train_orgs = X_train[provider_col].unique()
    train_orgs.sort()
    test_orgs = X_test[provider_col].unique()
    test_orgs.sort()

    print(f"\nTrain orgs: {train_orgs}")
    print(f"\nTest orgs: {test_orgs}")

    print(f"\nTrain column data: {X_train.shape}")
    print(f"Test column data: {X_test.shape}")

    return X_train, X_test


X_train, X_test = split_data(data, 'Data provider', test_size=0.2, random_state=42)


Orgs which don't seem to be subsidiaries ...



Data provider  count   org_parent
1                                                  immap    221        immap
2                                                    hdx    139          hdx
5            hera-humanitarian-emergency-response-africa    100         hera
11                                                redhum     69       redhum
13                                            fieldsdata     53   fieldsdata
17                                                  ifrc     49         ifrc
20                                                   wfp     41          wfp
25                                           brcmapsteam     31  brcmapsteam
28                                                   dhs     28          dhs
29                                    standby-task-force     28      standby
30                                                 clear     26        clear
37                                    insecurity-insight     17   insecurity
44                                               un-ocha     15           un
46                               education-cluster-yemen     13    education
49                                                  iati     12         iati
50                                              crs-waro     11          crs
51                                            hrrp-nepal     11         hrrp
53                                                  qcri     10         qcri
54                                global-shelter-cluster     10       global
55                                                  cbes     10         cbes
57                                                 meers      9        meers
58                             water-point-data-exchange      9        water
60                                                  cerf      9         cerf
62                 undp-human-development-reports-office      8         undp
63                                                  awsd      8         awsd
64                                                 cpaor      8        cpaor
65                       inter-sector-coordination-group      8        inter
66                                                  cred      7         cred
67                                                 lacso      7        lacso
68                                           interaction      7  interaction
70                                 netherlands-red-cross      6  netherlands
71                                                 cesvi      6        cesvi
72                                           ourairports      6  ourairports
74                                                   gec      6          gec
76                  eth-zurich-weather-and-climate-risks      5          eth
77                                            cirrolytix      5   cirrolytix
79         unrwa-for-palestine-refugees-in-the-near-east      5        unrwa
81                                                   rca      5          rca
82                                        health-cluster      5       health
83                                                   hxl      5          hxl
84                                                   idi      5          idi
85                                      libya-ingo-forum      5        libya
86                                               jhucsse      5      jhucsse
87                                                 ewipa      4        ewipa
89                              moving-energy-initiative      4       moving
90                                               dalberg      4      dalberg
91                                         cfp-rco-nepal      4          cfp
92                                                unesco      3       unesco
93                                                 unodc      3        unodc
95                                                  cimp      3         cimp
98                                                srsgcc      3       srsgcc
99                                somal

Train orgs: ['cerf', 'netherlands-red-cross', 'ocha-burundi', 'world-health-organization', 'ocha-roap', 'ocha-iraq', 'ourairports', 'ocha-mozambique-hat', 'ocha-libya', 'water-point-data-exchange', 'ocha-dr-congo', 'soswcaf', 'ocha-philippines', 'health-cluster', 'idi', 'lacso', 'ocha-rowca', 'ocha-fiss', 'ocha-cameroon', 'ocha-myanmar', 'fao-reowa', 'cbes', 'ocha-somalia', 'ifrc', 'standby-task-force', 'ocha-yemen', 'clear', 'insecurity-insight', 'ocha-opt', 'eth-zurich-weather-and-climate-risks', 'ocha-indonesia', 'libya-ingo-forum', 'ipc-cluster-guinea', 'world-bank-group', 'hdx', 'jcc', 'cpaor', 'gec', 'unrwa-for-palestine-refugees-in-the-near-east', 'ocha-ethiopia', 'ocha-colombia', 'ocha-chad', 'sadc_rvaa', 'srsgcc', 'ocha-haiti', 'ocha-eritrea', 'iati', 'ocha-afghanistan', 'brcmapsteam', 'ocha-turkey', 'kenya-national-bureau-of-statistics', 'ocha-mali', 'rcpwca', 'hera-humanitarian-emergency-response-africa', 'undp-human-development-reports-office', 'cesvi', 'ocha-rosc', 'unhcr'

### Create prompt files

In [45]:
def create_prompt_file(X_train, prompt_col, filename):
    """
    Create a prompt file from a DataFrame.

    Args:
        X_train (pd.DataFrame): The DataFrame containing the prompts.
        prompt_col (str): The name of the column containing the prompts.
        filename (str): The name of the file to write the prompts to.
    """

    with open(filename, 'w') as f:
        for index, row in X_train.iterrows():
            f.write(row[prompt_col] + "\n")

    print(f"Prompts written to {filename}")

def generate_completion_prompt(dataset_name, resource_name, column_name, excerpt, hxl_tag=None, add_response=True):
    """
    Generate a completion (eg Davinci) fine-tuning prompt for HXL tags given dataset, resource, column information.

    Parameters:
    - dataset_name (str): Name of the dataset.
    - resource_name (str): Name of the resource.
    - column_name (str): Name of the column.
    - excerpt (str): Examples or excerpt of the column.
    - hxl_tag (str, optional): HXL tags for the column. Default is None.
    - add_response (bool, optional): Whether to include the response in the prompt. Default is True.

    Returns:
    - dict: A dictionary containing the prompt and optional completion/response.
    """
    resource_name = resource_name.replace(f"{LOCAL_DATA_DIR}/",'')
    #column_details = f"dataset_name:'{dataset_name}'; resource_name='{resource_name}'; column_name:{column_name}; examples:{excerpt}"
    column_details = f"resource_name='{resource_name}'; column_name:'{column_name}'; examples:{excerpt}"

    prompt = {"prompt": f"What are the HXL tags for a column with these attributes? {column_details}"}
    if add_response:
        prompt["completion"] = f"{hxl_tag}"
    return prompt

def generate_chat_prompt(dataset_name, resource_name, column_name, excerpt, hxl_tag=None, add_response=True):
    """
    Generate a chat (eg for GPT-3.5-Turbo) fine tuning prompt for HXL tags given dataset, resource, column information.

    Parameters:
    - dataset_name (str): Name of the dataset.
    - resource_name (str): Name of the resource.
    - column_name (str): Name of the column.
    - excerpt (str): Examples or excerpt of the column.
    - hxl_tag (str, optional): HXL tags for the column. Default is None.
    - add_response (bool, optional): Whether to include the response in the prompt. Default is True.

    Returns:
    - dict: A dictionary containing the prompt and optional completion/response.
    """

    system_message = """
        You are an assistant that replies with HXL tags and attributes"
    """

    resource_name = resource_name.replace(f"{LOCAL_DATA_DIR}/",'')
    #column_details = f"dataset_name:'{dataset_name}'; resource_name='{resource_name}'; column_name:{column_name}; examples:{excerpt}"
    column_details = f"resource_name='{resource_name}'; column_name:'{column_name}'; examples:{excerpt}"

    user_prompt = f"What are the HXL tags and attributes for a column with these details? {column_details}"

    prompt = {
        "messages": [
            {"role": "system", "content": system_message},
            {"role": "user", "content": user_prompt},
        ]
    }

    if add_response:
        prompt["messages"].append({"role": "assistant", "content": hxl_tag})

    #prompt = json.dumps(prompt)

    return prompt

def generate_prompts(df,
                     heading_col='Text header',
                     resource_name_col='File', \
                     tag_col='Hashtag with Attributes', \
                     excerpt_col='Data excerpt', \
                     hxl_tag=False,
                     prompt_type='completion'):
    """
    Generate a set of prompts for HXL tags from a DataFrame.

    Parameters:
    - df (DataFrame): Input DataFrame containing dataset, resource, column information.
    - hxl_tag (bool, optional): Whether to include HXL tags in the prompts. Default is False.
    - completion_prompt (string): One of 'completion', 'chat'

    Returns:
    - str: A string containing JSON-formatted prompts.
    """
    allowed_prompt_types =  ['completion', 'chat']
    if prompt_type not in allowed_prompt_types:
        print(f"Prompt type {prompt_type} is not one of {allowed_prompt_types}!")
        sys.exit()

    prompts = []
    for index, row in df.iterrows():
        if prompt_type == 'completion':
            prompt = generate_completion_prompt('',  # Dataset name
                                    row[resource_name_col], \
                                    row[heading_col], \
                                    row[excerpt_col], \
                                    hxl_tag=row[tag_col], \
                                    add_response=True)
        elif prompt_type == 'chat':
            prompt = generate_chat_prompt('',  # Dataset name
                        row[resource_name_col], \
                        row[heading_col], \
                        row[excerpt_col], \
                        hxl_tag=row[tag_col], \
                        add_response=True)

        prompts.append(prompt)
    return prompts

def save_prompts(prompts, filename):

    with open(filename, 'w') as f:
        for prompt in prompts:
            f.write(json.dumps(prompt) + "\n")

    print(f"Prompts written to {filename}")

# Prompt for use with davinci-002
#completion_prompts = generate_prompts(X_train, hxl_tag=False, prompt_type='completion')
#save_prompts(completion_prompts, f"{LOCAL_DATA_DIR}/hxl_completion_prompts.jsonl")


# Prompt for use with GPT-3.5-Turbo or GPT-4o-mini
chat_prompts = generate_prompts(X_train, hxl_tag=True, prompt_type='chat')
save_prompts(chat_prompts, f"{LOCAL_DATA_DIR}/hxl_chat_prompts.jsonl")


Prompts written to /content/drive/MyDrive/Colab/hxl-metadata-prediction/data//hxl_chat_prompts.jsonl
